In [7]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [8]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [9]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [10]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
iay_radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [11]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [12]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[5:6]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    #Start Chrome
    driver.get(url)
    #Year Selection
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(".//option[@value='0']").click()
    year_query = ".//option[@value='" + year['value'] + "']"
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    
    #DataStore
    df_list = []
    
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, iay_radio_name))
    )
    element.click()
    
    #state select
    check_table()
    temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
    states = []
    for row in temp_list:
        try:
            x = {}
            td = row.find_elements_by_xpath(".//td")[1]
            x['name'] = td.text
            x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
            states.append(x)
        except Exception as e:
            print("Error while parsing table data |", e)
    for state in states:
        print("----Scrapping data for State: ", state['name'])
        driver.get(state['link'])
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
        districts = []
        for row in temp_list:
            x = {}            
            x['name'] = row.find_elements_by_xpath(".//td")[1].text
            x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
            districts.append(x)
        for district in districts:
            print("------Scrapping data for District: ", district['name'])
            driver.get(district['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            blocks = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                blocks.append(x)
            
            for block in blocks:
                print("--------Scrapping data for Block: ", block['name'])
                driver.get(block['link'])
                check_table()
                html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                df = pd.read_html(html_table, header=3)[0]
                df = df[:-1]
                #df.columns = table_head
                df['Financial Year'] = year['text']
                df['State Name'] = state['name']
                df['District Name'] = district['name']
                df['Block Name'] = block['name']
                df_list.append(df)
                #except Exception as e:
                #    print("Error while table data |", e)
                
    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2015-2016', 'value': '2015-2016 '}]
--Scrapping data for Year:  2015-2016
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=66.0.3359.181)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
------Scrapping data for District:  BAKSA
--------Scrapping data for Block:  Barama
--------Scrapping data for Block:  Baska
--------Scrapping data for Block:  Dhamdhama
--------Scrapping data for Block:  Gobardhana(BTC)
--------Scrapping data for Block:  Goreswar
--------Scrapping data for Block:  Jalah(BTC)
--------Scrapping data for Block:  Nagrijuli
--------Scrapping data for Block:  Tamulpur
------Scrapping data for District:  BARPETA
--------Scrapping data for Block:  BAJALI
--------Scrapping data for Block:  BARPETA
--------Scrappi

--------Scrapping data for Block:  NARAYANPUR
--------Scrapping data for Block:  NOWBOICHA
--------Scrapping data for Block:  TELAHI
------Scrapping data for District:  Morigaon
--------Scrapping data for Block:  BHURBANDHA
--------Scrapping data for Block:  KAPILI
--------Scrapping data for Block:  LAHARIGHAT
--------Scrapping data for Block:  MAYONG
--------Scrapping data for Block:  MOIRABARI
------Scrapping data for District:  NAGAON
--------Scrapping data for Block:  Bajiagaon
--------Scrapping data for Block:  Barhampur
--------Scrapping data for Block:  Batadraba
--------Scrapping data for Block:  Binakandi
--------Scrapping data for Block:  Dhalpukhuri
--------Scrapping data for Block:  Dolongghat
--------Scrapping data for Block:  Jugijan
--------Scrapping data for Block:  Juria
--------Scrapping data for Block:  Kaliabor
--------Scrapping data for Block:  Kathiatoli
--------Scrapping data for Block:  Khagorijan
--------Scrapping data for Block:  Lowkhowa
--------Scrapping dat

--------Scrapping data for Block:  KIRATPUR
--------Scrapping data for Block:  KUSHESHWAR ASTHAN
--------Scrapping data for Block:  KUSHESWAR ASTHAN EAST
--------Scrapping data for Block:  MANIGACHHI
--------Scrapping data for Block:  SINGHWARA
--------Scrapping data for Block:  TARDIH
------Scrapping data for District:  GAYA
--------Scrapping data for Block:  AMAS
--------Scrapping data for Block:  ATRI
--------Scrapping data for Block:  BANKEY BAZAR
--------Scrapping data for Block:  BARACHATTI
--------Scrapping data for Block:  BATHANI
--------Scrapping data for Block:  BELAGANJ
--------Scrapping data for Block:  BODHGAYA
--------Scrapping data for Block:  DOBHI
--------Scrapping data for Block:  DUMARIA
--------Scrapping data for Block:  FATEHPUR
--------Scrapping data for Block:  GURARU
--------Scrapping data for Block:  GURUA
--------Scrapping data for Block:  IMAMGANJ
--------Scrapping data for Block:  KHIZARSARAI
--------Scrapping data for Block:  KONCH
--------Scrapping data f

--------Scrapping data for Block:  Kowakole Block
--------Scrapping data for Block:  Meskaur Block
--------Scrapping data for Block:  Nardiganj Block
--------Scrapping data for Block:  NARHAT BLOCK
--------Scrapping data for Block:  Nawada Block
--------Scrapping data for Block:  Pakaribarawan
--------Scrapping data for Block:  Rajauli Block
--------Scrapping data for Block:  Roh Block
--------Scrapping data for Block:  SIRDALA
--------Scrapping data for Block:  Warsaliganj
------Scrapping data for District:  PASHCHIM CHAMPARAN
--------Scrapping data for Block:  BAGAHA-I
--------Scrapping data for Block:  BAGAHA-II
--------Scrapping data for Block:  BAIRIA
--------Scrapping data for Block:  BETTIAH
--------Scrapping data for Block:  BHITAHA
--------Scrapping data for Block:  CHANPATIA
--------Scrapping data for Block:  GAUNAHA
--------Scrapping data for Block:  JOGAPATTI
--------Scrapping data for Block:  LAURIYA
--------Scrapping data for Block:  MADHUBANI
--------Scrapping data for B

--------Scrapping data for Block:  PARIHAR
--------Scrapping data for Block:  Parsauni
--------Scrapping data for Block:  PUPRI
--------Scrapping data for Block:  RIGA
--------Scrapping data for Block:  RUNNISAIDPUR
--------Scrapping data for Block:  SONBARSA
--------Scrapping data for Block:  Suppi
--------Scrapping data for Block:  SURSAND
------Scrapping data for District:  SIWAN
--------Scrapping data for Block:  ANDAR
--------Scrapping data for Block:  BARHARIA
--------Scrapping data for Block:  BASANTPUR
--------Scrapping data for Block:  BHAGWANPUR HAT
--------Scrapping data for Block:  DARAULI
--------Scrapping data for Block:  DARAUNDHA
--------Scrapping data for Block:  GORIAKOTHI
--------Scrapping data for Block:  GUTHANI
--------Scrapping data for Block:  HASANPUR
--------Scrapping data for Block:  HUSSAINGANJ
--------Scrapping data for Block:  JIRADEI
--------Scrapping data for Block:  LAKRI NABIGANJ
--------Scrapping data for Block:  MAHARAJGANJ
--------Scrapping data for

...

--------Scrapping data for Block:  Cheepurupalle
--------Scrapping data for Block:  Dattirajeru
--------Scrapping data for Block:  Denkada
--------Scrapping data for Block:  Gajapathinagaram
--------Scrapping data for Block:  Gantyada
--------Scrapping data for Block:  Garividi
--------Scrapping data for Block:  Garugubilli
--------Scrapping data for Block:  Gummalakshmipuram
--------Scrapping data for Block:  Gurla
--------Scrapping data for Block:  Jami
--------Scrapping data for Block:  Jiyyamma Valasa
--------Scrapping data for Block:  Komarada
--------Scrapping data for Block:  Kothavalasa
--------Scrapping data for Block:  Kurupam
--------Scrapping data for Block:  Lakkavarapukota
--------Scrapping data for Block:  Makkuva
--------Scrapping data for Block:  Mentada
--------Scrapping data for Block:  Merakamudidam
--------Scrapping data for Block:  Nellimarla
--------Scrapping data for Block:  Pachipenta
--------Scrapping data for Block:  Parvathipuram
--------Scrapping data for B

------Scrapping data for District:  Haveri
--------Scrapping data for Block:  Byadagi
--------Scrapping data for Block:  Hanagal
--------Scrapping data for Block:  Haveri
--------Scrapping data for Block:  Hirekerur
--------Scrapping data for Block:  Ranebenur
--------Scrapping data for Block:  Savanur
--------Scrapping data for Block:  Shiggaon
------Scrapping data for District:  Kalaburagi
--------Scrapping data for Block:  Afzalpur
--------Scrapping data for Block:  Aland
--------Scrapping data for Block:  Chincholi
--------Scrapping data for Block:  Chittapur
--------Scrapping data for Block:  Jewargi
--------Scrapping data for Block:  Kalaburagi
--------Scrapping data for Block:  Sedam
------Scrapping data for District:  Kodagu
--------Scrapping data for Block:  Madikeri
--------Scrapping data for Block:  Somwarpet
--------Scrapping data for Block:  Virajpet
------Scrapping data for District:  Kolar
--------Scrapping data for Block:  Bangarpet
--------Scrapping data for Block:  Ko

--------Scrapping data for Block:  ALAMPUR
--------Scrapping data for Block:  DHARUR
--------Scrapping data for Block:  GADWAL
--------Scrapping data for Block:  GHATTU
--------Scrapping data for Block:  ITIKYAL
--------Scrapping data for Block:  MALDAKAL
--------Scrapping data for Block:  MANOPADU
--------Scrapping data for Block:  WADDEPALLE
------Scrapping data for District:  KAMAREDDY
--------Scrapping data for Block:  BANSWADA
--------Scrapping data for Block:  BHIKNUR
--------Scrapping data for Block:  BICHKUNDA
--------Scrapping data for Block:  BIRKOOR
--------Scrapping data for Block:  DOMAKONDA
--------Scrapping data for Block:  GANDHARI
--------Scrapping data for Block:  JUKKAL
--------Scrapping data for Block:  KAMAREDDY
--------Scrapping data for Block:  LINGAMPET
--------Scrapping data for Block:  MACHAREDDY
--------Scrapping data for Block:  MADNUR
--------Scrapping data for Block:  NAGA REDDIPET
--------Scrapping data for Block:  NIZAM SAGAR
--------Scrapping data for B

--------Scrapping data for Block:  PEDDA ADISERLAPALLE
--------Scrapping data for Block:  PEDDAVURA
--------Scrapping data for Block:  SALIGOURARAM
--------Scrapping data for Block:  THIPPARTHI
--------Scrapping data for Block:  THRIPURARAM
--------Scrapping data for Block:  VEMULAPALLE
------Scrapping data for District:  NIRMAL
--------Scrapping data for Block:  BHAINSA
--------Scrapping data for Block:  DILAWARPUR
--------Scrapping data for Block:  KADDAMPEDDUR
--------Scrapping data for Block:  KHANPUR
--------Scrapping data for Block:  KUBEER
--------Scrapping data for Block:  KUNTALA
--------Scrapping data for Block:  LAXMANCHANDA
--------Scrapping data for Block:  LOHESRA
--------Scrapping data for Block:  MAMDA
--------Scrapping data for Block:  MUDHOLE
--------Scrapping data for Block:  NIRMAL
--------Scrapping data for Block:  SARANGAPUR
--------Scrapping data for Block:  TANUR
------Scrapping data for District:  NIZAMABAD
--------Scrapping data for Block:  ARMUR
--------Scrap

------Scrapping data for District:  WARANGAL (URBAN)
--------Scrapping data for Block:  BHEEMADEVARPALLE
--------Scrapping data for Block:  DHARMASAGAR
--------Scrapping data for Block:  ELKATHURTHI
--------Scrapping data for Block:  HANAMKONDA
--------Scrapping data for Block:  HASANPARTHY
--------Scrapping data for Block:  KAMALAPUR
------Scrapping data for District:  YADADRI
--------Scrapping data for Block:  ALAIR
--------Scrapping data for Block:  ATMAKUR (M)
--------Scrapping data for Block:  BHUVANAGIRI
--------Scrapping data for Block:  BIBINAGAR
--------Scrapping data for Block:  BOMMALARAMARAM
--------Scrapping data for Block:  CHOUTUPPAL
--------Scrapping data for Block:  M TURKAPALLE
--------Scrapping data for Block:  MOTHKUR
--------Scrapping data for Block:  NARAYANAPUR
--------Scrapping data for Block:  POCHAMPALLE
--------Scrapping data for Block:  RAJAPET
--------Scrapping data for Block:  RAMANNAPETA
--------Scrapping data for Block:  VALIGONDA
--------Scrapping data 